In [233]:
import pandas as pd
import numpy as np
from astropy.coordinates import SkyCoord,FK5
import astropy.units as u
import ads
import bibtexparser
from pybtex.database import parse_string,parse_file
from pybtex.style.formatting import BaseStyle
from pybtex.richtext import Text, Tag
from astropy.cosmology import FlatLambdaCDM

In [2]:
ads.config.token="BmHSdCx8G5f7anbkQmdQIYc4xvlTQZasPuFecWaF"

In [86]:
ml_df=pd.read_csv("XJETS-master - master_list.csv",sep=',')


In [343]:
ml_df['Name2']=ml_df.apply(lambda row:row['Name'] if row['Name']!=row['IAU name'] 
                                  else row['alternate_name'] if row['alternate_name'] is not None
                                  else row['IAU name'],axis=1)
#ml_df['Name3']='\\object{'+ml_df['Name2']+'}'
ml_df['angular_scale']=round(ml_df["scale kpc/''"],2)
ml_df['z2']=round(ml_df["z"],3)
ml_df['z2']=ml_df['z2'].apply(lambda x: f'{x:.3f}')
ml_df['low_count']=ml_df['low-count']
ml_df['bapp2']=round(ml_df['b_app'],2)
ml_df['Core L1.4']=round(ml_df['Core L1.4'],2)
ml_df['Lobe L300']=round(ml_df['Lobe L300'],2)

ml_df=ml_df[~ml_df['citation'].isna()]
ra_dec=ml_df['ra']+' '+ml_df['dec']
ra_dec2=SkyCoord(ra_dec.values, frame=FK5, unit=(u.hourangle, u.deg))
ml_df['ra2']=[ang.ra.to_string(u.hour,sep=':',alwayssign=True,pad=True,precision=1) for ang in ra_dec2]
ml_df['dec2']=[ang.dec.to_string(u.deg,sep=':',alwayssign=True,pad=True,precision=1) for ang in ra_dec2]


In [344]:
ml_df['ads_refs']=ml_df['ads_links'].apply(lambda x: x if pd.isna(x) else list(filter(None,x.split("http://adsabs.harvard.edu/abs/") )))

In [345]:
all_refs=sum(ml_df['ads_refs'].dropna().values,[])
all_refs2=[]
for ref in all_refs:
    fmt=''.join(c for c in ref if c  not in ',')
    fmt="\\"+f'cite{{{fmt}}}'
    all_refs2.append(fmt)

In [346]:
np.savetxt('old_refs.tex',all_refs2,fmt="%s")

In [347]:
with open('all_refs.bib') as bib_file:
    articles=bibtexparser.bparser.BibTexParser(common_strings=True).parse_file(bib_file)


Overwritting existing string for key: june.


In [348]:
def format_ref(refs):
    if type(refs)!=list:
        return np.nan
    r=[]
    for ref in refs:
        r.append(''.join(c for c in ref if c  not in ','))
    return r
ml_df['ads_refs2']=ml_df['ads_refs'].apply(lambda x: format_ref(x))

In [349]:
rows=[]
for index,row in ml_df[['Name2','ads_refs2']].dropna().iterrows():
    #print(row)
    for bibcode in row['ads_refs2']:
        
        a=articles.get_entry_dict()[bibcode]
        auth=a['author']
        strs='{}~'
        auth=''.join(c for c in auth if c not in strs)
        name=row['Name2']
        number=f'{(a["number"])}' if 'number' in a else ''
        title=''.join(c for c in a['title'] if c not in strs)
        
        rows.append([name,auth,a['year'],title,a['journal'],a['volume'],a['adsurl'],number,a['pages']])
        
        
        

In [350]:
ref_df=pd.DataFrame(rows,columns=["Name2","author","year","title","journal","volume","link","number","pages"])


In [351]:
ref_df.shape

(178, 9)

In [352]:
articles.get_entry_dict()['2004ApJ...612..729H']

{'year': '2004',
 'volume': '612',
 'title': '{The Origins of X-Ray Emission from the Hot Spots of FR II Radio Sources}',
 'primaryclass': 'astro-ph',
 'pages': '729-748',
 'number': '2',
 'month': 'September',
 'keywords': 'Galaxies: Active, Galaxies: Quasars: General, Radiation Mechanisms: Nonthermal, X-Rays: Galaxies, Astrophysics',
 'journal': '\\apj',
 'eprint': 'astro-ph/0405516',
 'doi': '10.1086/422808',
 'author': '{Hardcastle}, M.~J. and {Harris}, D.~E. and {Worrall}, D.~M. and {Birkinshaw}, M.',
 'archiveprefix': 'arXiv',
 'adsurl': 'https://ui.adsabs.harvard.edu/abs/2004ApJ...612..729H',
 'adsnote': 'Provided by the SAO/NASA Astrophysics Data System',
 'ENTRYTYPE': 'article',
 'ID': '2004ApJ...612..729H'}

In [353]:
rows2=[]
for index,row in ml_df[pd.isna(ml_df['ads_refs2'])][['Name2','ads_refs2','citation']].iterrows():
    bib=row['citation'].split('{')[1]
    bib=bib.split('}')[0]
    a=articles.get_entry_dict()[bib]
    auth=a['author']
    strs='{}~'
    auth=''.join(c for c in auth if c not in strs)
    name=row['Name2']
    number=f'{(a["number"])}' if 'number' in a else ''
    title=''.join(c for c in a['title'] if c not in strs)

    
    rows2.append([name,auth,a['year'],title,a['journal'],a['volume'],a['adsurl'],number,a['pages']])

In [354]:
ref_df2=pd.DataFrame(rows2,columns=["Name2","author","year","title","journal","volume","link","number","pages"])


In [355]:
ref_df_all['journal'].unique()

array(['\\apj', '\\mnras', '\\aap', '\\apjs', '\\aj', '\\apjl',
       'Astronomische Nachrichten', '\\nat'], dtype=object)

In [356]:
ref_df_all=pd.concat([ref_df,ref_df2])

In [357]:
ref_df_all['journal2']=ref_df_all['journal'].map({"\\apj":'ApJ','\\mnras':'MNRAS','\\apjs':'ApJS'
                                                  ,'\\aj':'AJ','\\apjl':'ApJL'
                                                  ,'\\nat':'Nature'
                                                  ,'Astronomische Nachrichten':'Astronomische Nachrichten'
                                                 ,'\\aap':'A&A'})

In [358]:
ref_df_all.to_csv('all_refs.csv',index=False)

In [359]:
cosmo = FlatLambdaCDM(H0=67.8,Om0=0.308)
ml_df['distance2']=cosmo.luminosity_distance(ml_df['z']).value
ml_df['distance2']=ml_df['distance2'].apply(lambda x:round(x,2))
ml_df['angular_scale2']=cosmo.arcsec_per_kpc_proper(ml_df['z']).value
ml_df['angular_scale2']=ml_df['angular_scale2'].apply(lambda x:round(1/x,2))
ml_df['bapp3']=ml_df['bapp2'].apply(lambda x: '' if pd.isna(x) else f'{x:.2f}')

In [360]:
ml_df2=ml_df[['Name2','IAU name','ra2','dec2','z2'
              ,'bapp3','angular_scale2'
              ,'distance2','class','X-Ray features'
             ,'Core L1.4','Lobe L300']].copy(deep=True)
ml_df2['Name']=ml_df['Name2']

ml_df2[['Name','IAU name','ra2','dec2','z2','bapp3','angular_scale2','distance2','class','X-Ray features',
       'Core L1.4','Lobe L300']].sort_values(by=['ra2']).to_csv('new_master_list.csv',index=False)

In [297]:
col_attr = 'XJETS-master - col_name_attributes_new.csv'
cl_attr_df=pd.read_csv(col_attr).set_index('attribute')

In [298]:
cl_attr_df

Name  IAU name          bapp3         ra2         dec2  \
attribute                                                                     
pretty_name   Source Name  IAU Name  Beta apparent  Ra (J2000)  Dec (J2000)   
use_as_scale            0         0              1           0            0   
use_as_cat              0         0              0           0            0   
valid_axis              0         0              1           0            0   

             z2       distance2 angular_scale2  class  X-Ray features  
attribute                                                              
pretty_name   z  Distance (Mpc)  Scale(kpc/'')  Class  X-Ray features  
use_as_scale  1               1              0      0               0  
use_as_cat    0               0              0      0               0  
valid_axis    1               1              1      0               0